## Security topics

- Vectors of attack review
- Passwords and encryption types
- Password cracking exercise
- Network ssh brute force attacks
- TCP wrappers
- Pluggable authentication module (PAM)
- Two factor authentication
- Stack overflow vulnerabilities
- Package upgrade and verification
- Network ports
- Traffic sniffing with tcpdump
- Iptables
- Open port scanning

<hr>

## Examples of how systems get compromised.


![How systems get compromized](img/system_compromise.gif)


- Cracked, stollen and sniffed passwords
- SSH client with a sniffer on a multi-user system: reads user name, password and the destination host.
- SSH brute force attack guesses user credentials.
- Accounts with empty passwords and root privileges
- World writable files and directories can be used for planting trojans.
- SETUID and SETGID executables
- Trojans 
- Stack overflow attacks on vulnerable services
- Worms

<hr>

## Linux passwords.


On a local system, passwords are stored in file `/etc/shadow`:


`mike:$6$A0NKorlZ$l3YhLlm/Y1n2BW0YBiryNl5cS6vx5k.4j4LE/vb5FUOnD.uVXkiUA1kPSHLo5/6q5MzEJTal1OY1OiE4ReSpK0:17317:0:99999:7:::`

The second field consits of 3 parts: the hashing algorithm, $6$, the salt $A0NKorlZ$, and the hashing function, crypt, value of (password,salt) parameters, 

`l3YhLlm/Y1n2BW0YBiryNl5cS6vx5k.4j4LE/vb5FUOnD.uVXkiUA1kPSHLo5/6q5MzEJTal1OY1OiE4ReSpK0`

The password hash is generated by function crypt. From the output of man crypt we see the hash structure components:

`$id$salt$encrypted`

           The following values of id are supported:

           ID(prefix) | Method
           ------------------------------------------------------------
                  1   | MD5
                  2a  | Blowfish (not in mainline glibc; added in some
                      | Linux distributions)
                  5   | SHA-256 (since glibc 2.7)
                  6   | SHA-512 (since glibc 2.7)
                  y   | yescrypt, hash size 256 bits, salt size up to 512 bits

So   `$5$salt$encrypted`   is   an   SHA-256   encoded    password    and
`$6$salt$encrypted` is an SHA-512 encoded one.

<hr> 

## MD5, SHA256, and SHA512 Encryption algorithms.


- The crypt algorithms are the one way function. There is no reverse function to derive the original password from its hash.
- md5-crypt can be divided into three phases. Initialization, loop, and finalization:

              1. Generate a simple md5 hash based on the salt and password
              2. Loop 1000 times, calculating a new md5 hash based on the previous hash concatenated with 
                 alternating the password and the salt.
              3. Use a special base64 encoding on the final hash to create the password hash string
- sha512-crypt allows to specify a custom number of rounds, from 1000 to 999999999. the default is 5000.

<hr>

## cryptvm VM setup (Exercise).


Clone your kvm1 virtual machine into a new VM, cryptvm.
```bash
virsh shutdown kvm1
virt-clone -o kvm1 -n cryptvm -f /home/hostadm/KVM/cryptvm.qcow2
```

Start cryptvm and login to its console:
```bash
virsh start cryptvm
virsh console cryptvm
```
Fix the hostname in `/etc/hostname` and reset the machine ID by running the script:
```bash
./vm_id_reset.sh
```
Reboot the VM.

On the desktop, enter the IP address of cryptvm in `/etc/hosts` file to reslove its host name.

Create user mike1:
```bash
groupadd -g 1002 mike1
useradd -m -s /bin/bash -g mike1 -u 1002 mike1
```

<hr>

## User password with different encryptions (Exercise).

On the desktop, install python module passlib:

```bash
conda install passlib
```

In Python, we'll setup 4 user names, mike1, mike2, mike3, and mike4 with password mike123, encrypted 
 with 4 different algorithms: DES, MD5, SHA256, and SHA512, accordingly.
 
Open Jupyter notebook, and paste the following content in the cell:


In [2]:
from passlib.context import CryptContext

# Users mike1, mike2, mike3, and mike3 with different password encryption algorithms
users = { 'mike1':'des_crypt', 
          'mike2':'md5_crypt', 
          'mike3':'sha256_crypt',
          'mike4':'sha512_crypt' }

# Password and salt
passwd = 'mike123'
salt_add = 'b1b2'

# Initialize list for password hashes
out_passwd = []

# DES hash
ctx = CryptContext(schemes=users['mike1'])
hash = ctx.hash(passwd)
out_passwd.append(f'mike1:{hash}')

# MD5 hash
ctx = CryptContext(schemes=users['mike2'])
hash = ctx.hash(passwd, salt=salt_add)
out_passwd.append(f'mike2:{hash}')

# SHA hashes
for i in sorted(users)[2:]:
    ctx = CryptContext(schemes=users[i])
    hash = ctx.hash(passwd, salt=salt_add,rounds=5000)
    out_passwd.append(f'{i}:{hash}')

# Save password hashes in file passwd.txt
with open('passwd.txt','w') as f:
    for i in out_passwd:
        f.write(f'{i}\n')
        
# Check the content of file passwd.txt
%cat passwd.txt

mike1:JGwPbJHxq/Xrs
mike2:$1$b1b2$b1ELOdgDydgNqFTzZPEWn.
mike3:$5$b1b2$Tm93dbH8yrvOLawhu5c3pDV5YBYoFFP4ndArlklRyeA
mike4:$6$b1b2$7.mG4cQmg8y.10Ncsi.nndGMVybyaE6gnENYTKjF4qDF5mzMVhrTmJa.S1JdAef9TPTf.yWIt9r/LUCbwyA0l.


## Cracking passwords with John the Ripper (Exercise).


On cryptvm, install John the Ripper:
```bash
apt install john
mkdir john
cd john
```

Get file passwd.txt from the desktop:
```bash
scp 192.168.112.1:Python/passwd.txt .
```

Crack DES passwords (default):
```bash
john passwd.txt        #this cracks password
john --show passwd.txt #this shows  the cracked passwords
```
Crack MD5 passwords:
```bash
john --format=md5crypt passwd.txt      #this cracks password
john --show passwd.txt                 #this shows  the cracked passwords
```
They should look as follows:
```{addmonition} output
mike1:mike123
mike2:mike123

2 password hashes cracked, 2 left
```

Note, John the Ripper can't handle advanced encryption algorithms, SHA-256 and SHA-512.

<hr>

## SSH brute force attacks (Exercise)

On the VM, assign password ```mike123``` to user mike1:
```bash
sudo passwd mike1]
```


Install `crunch` package on the desktop, which is needed for generating a password dictionary.
```bash
sudo apt install crunch
```

Make `cryptvm` name resolvable by creating the entry in `/etc/hosts` file on the desktop.

On the desktop, generate a password table, `passwords.txt`, by running `crunch`:
```bash
crunch  7 7 mike123 -o passwords.txt
```
The above creates 7 symbol words combined from the letters and numbers provided.

Find the position of the correct password in the file:
```bash
grep -n mike123 passwords.txt
```
Shorten passwords.txt file to make the correct passwords to be within the first 10 lines for the scanner to 
complete its work faster>
If it, for example, shows 22876-th position. 
Remove the first 22870 line in the file with command ```sed```:
```bash
sed -i 1,22870d passwords.txt
```
Check the position of the correct password again:
```bash
grep -n mike123 passwords.txt
```

Install package ```hydra``` on the desktop:
```bash
sudo apt install hydra
```

Run SSH bruteforce attacks onto account mike1 on the both VMs:
```bash
hydra -l mike1 -P passwords.txt cryptvm ssh
```
Within a few minutes, hydra should be able to identify the correct password for user mike1 from `passwords.txt` list.

```{admonition} output
[22][ssh] host: cryptvm   login: mike1   password: mike123
```
<hr>

## Identifying SSH login attacks in the system logs (Exercise)
 

On `cryptvm` VM, check the lines in log file `auth.log` and see ssh login attempts to user account `mike1`:
```bash
grep mike1 /var/log/auth.log  | grep auth
```
See the successfull attempt to login:
```bash
grep mike1 /var/log/auth.log  | grep -E -v '(error|[Ff]ail)'
```

On a RedHat/Rocky system, the similar authentication logs go into file `/var/log/secure`

<hr>

## TCP Wrappers
 

Access to inetd startable services can be controlled through daemon tcpd; it reads the access rules from files `/etc/hosts.allow` and `/etc/hosts.deny`. Similarly, the access can be controlled for the other services, such as portmap, if they have been compiled with libwrap libraries.

Format of /etc/hosts.allow and `/etc/hosts.deny`:
```c
    service_list:  host_list
```

`/etc/hosts.allow` -- is checked first by tcpd: if the entries match, the host is allowed to access the service, otherwise, `/etc/hosts.deny` is checked -- if the entries match, the access is denied. If non of the entries match, or both the files are empty, the access is allowed.

Keywords: `ALL` (matches all requests), `EXCEPT`, `LOCAL` (hosts matching the local network - no domain), `KNOWN` (resolvable hosts), `PARANOID` (hostname doesn't match IP), `UNKNOWN` (unresolvable hosts).
Example:

```{admonition} etc/hosts.allow:
    sshd:       165.230.172.13  128.6.
    in.tftpd:   LOCAL, .my.domain
    portmap:    128.6.14.0/255.255.255.128
    ALL:        .foobar.edu EXCEPT terminalserver.foobar.edu
```

```{admonition} /etc/hosts.deny:
    ALL: ALL
```

<hr>


## ssh protection with TCP Wrappers (Exercise).


Login to the console of `cryptvm` VM:
```bash
virsh console cryptvm
```
Become root
```bash
sudo -s
```
Edit file `/etc/hosts.deny` and add the following entry:
```{admonition} /etc/hosts.deny
    ALL: ALL
```
Try SSH to cryptvm from your desktop.
```bash
ssh cryptvm
```
The SSH attempt should fail.
Edit file `/etc/hosts.allow` and add the following entry:
```{admonition} /etc/hosts.allow
sshd: 192.168.122.
```
Try to SSH to cryptvm from the desktop again.

<HR>

## Pluggable Authentication Module (PAM).

All the PAM configuration files are located in directory `/etc/pam.d`.

- Every application or service that uses PAM has its own config file there. Their entries consist of four columns:

| module type  | control flag |	module path  | argument |
| :- | :- | :- | :-|

- Module types

| auth | account | session | password |
| :- | :- | :- | :-|
| Authenticates a user |Restricts or permits access when certain conditions on the account are met | Some operations on the user environment at login and/or loogout | Needed when updating a user password |0

- The control flag specifies how PAM reacts on success or failure of the module.

| required |requisite |	sufficient |optional |
| :- | :- | :- | :-|
|Success of the module is required. If fails, doesn't exit until the other modules in the list are checked |Similar to required, but exits if the module fails | Exits if the module succeds | the success or failure of this module is only important if it is the only module in the stack associated with this service type. |

- Example `/etc/pam.d/sshd`:

```{admonition} /etc/pam.d/sshd:
    #Set correct type settings
    auth       required     pam_env.so envfile=/etc/default/locale
    # Standard Un*x authentication.
    @include common-auth

    # Disallow non-root logins when /etc/nologin exists.
    account    required     pam_nologin.so
    # Standard Un*x authorization.
    @include common-account

    # Standard Un*x session setup and teardown.
    @include common-session
    # Print the message of the day upon successful login.
    session    optional     pam_motd.so # [1]
    # Print the status of the user's mailbox upon successful login.
    session    optional     pam_mail.so standard noenv # [1]
    # Set up user limits from /etc/security/limits.conf.
    session    required     pam_limits.so

    # Standard Un*x password updating.
    @include common-password
```
***

## Two factor authentication (Exercise).

Using even a relatively strong password on a critical system may not be sufficient, especially, for remote access. Two-factor authentication, configurable through PAM, is desirable.

Do the following steps on ```cryptvm```:
```bash
sudo apt install libpam-google-authenticator
```


Add the following line into ```/etc/pam.d/sshd``` right after the line with ```@include common-auth```:
```{admonition} /etc/pam.d/sshd:
    auth required pam_google_authenticator.so
```

Edit file ```/etc/ssh/sshd_config.d/60-cloudimg-settings.conf``` and add
```{admonition} entry
   ChallengeResponseAuthentication yes
```
Restart ssh:
```bash
systemctl restart ssh
```
Configure the google authenticator by running command as user hostadm:
```bash
google-authenticator
```
    Do you want authentication tokens to be time-based (y/n) y

    Your new secret key is: 5G3KY2FPHDHF2GGY7MLQP6I4PA  - save the key. It will be needed for configuring the App.

    Do you want me to update your "/home/hostadm/.google_authenticator" file? (y/n) y

    Do you want to disallow multiple uses of the same authentication token?  (y/n) y

    This will permit for a time skew of up to 4 minutes between client and server. Do you want to do so? (y/n) y

    Do you want to enable rate-limiting? (y/n) n

It is possible to install the App from google on your phone, and/or plugins in chrome and firefox browsers for 
 dynamic one-time authentication codes. We won't be doing it as we don't have much time.

Try ssh to `cryptvm` from the desktop as hostadm and use both the password and one of the emergency scratch codes.

***

## Buffer overflow example 1.

A buffer overflow is the result of stuffing more data into a buffer than it can handle.

![](img/stack-ov.gif)

In the example, the program has a function with a typical buffer overflow coding error.
Dangerous functions for stack overflow (don't check the string boundaries): `strcat(), strcpy(), sprintf(), vsprintf(), gets(), scanf()`.

```c
#include <string.h>

void function(char *str) {

char buffer[16];

strcpy(buffer,str);
}


int main() {
char large_string[256];
int i;

for( i = 0; i < 255; i++)
large_string[i] = 'A';

function(large_string);
}

```


To exploit such flaw, an attacker would need to give a specially crafted encoded input. It can be done locally by using a rootkit or over a network by sending a packet with improperly advertised lengths.

<hr>

## Buffer overflow on a stack, example 2.
 

A code prompts for password, reads it from keyboard, and gives the root shell.

```c
#include <stdio.h>
#include <string.h>

int main()
{
    int setuid(); //Declare the type of the functions used below
    int system();
    int gets();

    char buff[10]; //Defines the input array buff of 10 Bytes size
    int pass = 0;

    printf("\n Enter the password : \n");
    gets(buff);

    if(strcmp(buff, "Password1") != 0)
    {
        printf ("\n Wrong Password \n");
    }
    else
    {
        printf ("\n Correct Password \n");
        pass = 1;
    }

    if(pass != 0)
    {
        printf ("pass=, %3d", pass); //See how variable 'pass' is corrupted

       /* Now Give root or admin rights to user*/
        printf ("\n Root privileges given to the user \n");

        setuid(0);
        system("/bin/bash");
    }

    return 0;
}
```

Any given password string, exceeding 11 letters, would corrupt the memory region, containing variable pass, therefore cause the code to give the root shell.

![](img/buffer_ovr.jpg)


<hr>

## Buffer overflow on Stack overflow exercise.

On `cryptvm`, download the source code and the Makefile:
```bash
wget http://linuxcourse.rutgers.edu/summer2023/html/security_remote/Downloads/root_shell.c
wget http://linuxcourse.rutgers.edu/summer2023/html/security_remote/Downloads/Makefile
```
Compile the source code, and assigne setuid root to the compiled executable:
```bash
make
sudo chown root:root root_shell
sudo chmod u+s root_shell
```
Run the executable:
```bash
./root_shell
```
When prompted for password, type in a long string:
    RRRRRRRRRRRRRRRRRRRR
Notice, you got the root shell.

The way to fix it: use function fgets instead of gets, for example:
```c
//gets(buff);
  fgets(buff,sizeof(buff),stdin);
```

<hr>

## Package upgrades and md5 checksum verification. (Exercise)

On `cryptvm` VM, run upgrades on regular bases and every time a new vulnerability discovered in installed packages:
```bash
apt update
apt upgrade
```
On a Rocky, you would use use `dnf` for updates: `dnf update`

Verify md5 checksum of downloaded software:
```bash
md5sum root_shell.c
```
Install package `tcpd`:
```bash
apt install tcpd
```

On `cryptvm` VM, install `dlocate` and verify `md5` checksum of the files installed with a package:
```bash
apt install dlocate
dlocate -md5sum tcpd
dlocate -md5check tcpd
```
On Rocky, one would  use `rpm -V` command to verify package integrity: `rpm -V tcp_wrappers`


<hr>

## Open Ports List. (Exercise)

Install package `net-tools` on `cryptvm` VM:
```bash
apt install net-tools
```
To see what ports are open, run command

```bash
netstat -nal
```
and check on TCP and UDP ports in the listing. To see what processes are bound to what ports, run as root
```bash
netstat -nalp | less
```

```{admonition} output:
    Active Internet connections (servers and established)
    Proto Recv-Q Send-Q Local Address       Foreign Address   State       PID/Program name
    tcp        0      0 0.0.0.0:515         0.0.0.0:*         LISTEN       1742/lpd Waiting
    tcp        0      0 127.0.0.1:25        0.0.0.0:*         LISTEN       1726/exim4
    tcp        0      0 192.168.1.101:1040  128.6.238.10:22   ESTABLISHED  2229/ssh
    tcp        0      0 192.168.1.101:1024  128.6.238.12:993  ESTABLISHED  2195/pine
    tcp6       0      0 :::22               :::*              LISTEN       1813/sshd
    udp        0      0 0.0.0.0:68          0.0.0.0:*                      2085/dhclient
```
Similarly,
```bash
netstat -n --inet --listening --programs
```
Also, the processes responsible for the open ports can be identified with
```bash
lsof -i
```
See example (Links to an external site.).

Syntax of `lsof`:
```c
    lsof -i [TCP|UDP][@host][:port]
```

To list all open files for specific processes:
```bash
lsof -p PID
lsof -c COMMAND
lsof -u username
```
To list all open files
```bash
lsof
```

Exercise

SSH to `cryptvm` VM from the desktop, become root, and run lsof to see the open internet ports:
```bash
ssh cryptvm
sudo -s
lsof -i -P
```
Note, option "-P" shows you the port number.

You should see the ports opened for the following services: `dhclient3, udp/68, sshd, tcp/22`.
If you have installed Samba in the previous class, you should also see the Samba related services with their ports, such as smbd, `tcp/137,138,139, tcp/445`, and `nmbd, udp/136,138`.

<hr>

## Closing ports by disabling network services.
 

- The open ports are related to the aplications/processes, which start either at the system startup or through inetd/xinetd.
For the Systemd aware applications,
```bash
systemctl stop service_name
systemctl disable service_name
```

- Vulnerable services:
`telnet, rsh, rcp, rexec, ftp, portmap, nfs, mountd, ypbind, ypserv`.
Disable them if your computer is on the open Internet. But if you need them, install a firewall and implement the tcp_wrappers.

- Relatively secure services:
Services protected with SSL libraries for encrypted connection such as `SSH, LDAP, Apache; Kerberos`.


<hr>

## Sniffing clear text traffic with tcpdump. (Exercise)


The classical FTP service is known to be ```clear text```, without encryption.

In this exercise we are going to install and run ```ftpd``` server on ```cryptvm```, connect via ftp from
 the desktop to ```cryptvm```, and sniff the netwoek traffic related to FTP via ```tcpdump```.

It is better to use ```tmux``` terminal server here for completing the tasks below on both ```cryptvm``` and 
 the desktop at the same time:
 
On ```cryptvm``` install ftpd:
```bash
sudo apt install ftpd
```
Verify that port tcp/21 is open:
```bash
netstat -na | grep "21 .* LISTEN"
```
On ```cryptvm```, install tcpdump:
```bash
sudo apt install tcpdump
```
On ```cryptvm``` start running tcpdump to sniff the traffic from the desktop, 192.168.122.1, to the destination port 21 (for ftpd):
```bash
sudo tcpdump -i enp1s0 src 192.168.122.1 and dst port 21 -A
```

On the desktop, install ftp client:
```bash
sudo install ftp
```
On the desktop, run ftp to ```cryptvm``` and authenticate as user mike1 with his password.
```bash
ftp cryptvm
```

Watch for the tcpdump output on ```cryptvm```. You should be able to see the user name and password in clear text:

```{admonition} among the output
   FTP: USER mike1
   FTP: PASS mike123
```

You can also type commands in the FTP prompt, like ```cd .ssh```, ```ls```, and see them in the output of tcpdump.

To exit from the FTP shell, type 
```bash
quit
```
***

## IP filtering firewalls (iptables)

Packet filtering is implemented through Linux Kernel.



![](img/filter.jpg) 

Chains for network packets:

    INPUT
    OUTPUT
    FORWARD
    
Chains are combined into tables:

    filter (default)
    NAT
    mangle
    
Each of the chains filters data packets based on
Source and Destination IP
Source and Destination Port number
Network interface
State of the packet
Target for the rule:

    ACCEPT
    DROP
    REJECT
    QUEUE
    RETURN
    LOG  
    
<hr>

## Simple iptables script



```{admonition} executable script:
    #!/bin/bash
    IPT=/sbin/iptables

    # Flush the tables
    $IPT -F INPUT
    $IPT -F OUTPUT
    $IPT -F FORWARD

    # Define default policy to DROP packets
    $IPT -P INPUT   DROP
    $IPT -P OUTPUT  DROP
    $IPT -P FORWARD DROP

    # Permit DNS traffic
    $IPT -A INPUT -p udp --sport 53 -j ACCEPT
    $IPT -A OUTPUT -p udp --dport 53 -j ACCEPT

    # Accept local-network return traffic from private network 192.168.122.0/24:
    $IPT -A INPUT -m state -p tcp --dport 1024:65535 --state ESTABLISHED,RELATED -s 192.168.122.0/24 -j ACCEPT
    $IPT -A OUTPUT -m state -p tcp --sport 1024:65535 ! --state INVALID -d 192.168.122.0/24 -j ACCEPT

    # Accept all HTTP connections
    $IPT -A INPUT -m state -p tcp --dport 80 ! --state INVALID -j ACCEPT
    $IPT -A OUTPUT -m state -p tcp --sport 80 --state ESTABLISHED,RELATED -j ACCEPT

    # Accept local (192.168.122.0/24) SSH traffic
    $IPT -A INPUT -m state -p tcp --dport 22 ! --state INVALID -s 192.168.122.0/24 -j ACCEPT
    $IPT -A OUTPUT -m state -p tcp --sport 22 --state ESTABLISHED,RELATED -d 192.168.122.0/24 -j ACCEPT

    # Accept all local (loopback) traffic on the lo interface
    $IPT -A INPUT -s 127.0.0.1 -i lo -j ACCEPT
    $IPT -A OUTPUT -d 127.0.0.1 -o lo -j ACCEPT

    # Log all other traffic
    $IPT -A INPUT -j LOG
    $IPT -A OUTPUT -j LOG
```

To check the current iptables rules, run
```bash
/sbin/iptables -n -L
```

<hr>


## Configuring iptables firewall (Exercise)

Make sure iptables have been installed on cryptvm VM:

```bash
dpkg -l | grep iptables
```

Check the `iptables` rules on `cryptvm`:

```bash
/sbin/iptables -n -L
```
On `cryptvm`, download the iptables script from `fw-script.sh` (Links to an external site.), make it executable, then run:
```bash
wget http://linuxcourse.rutgers.edu/summer2023/html/security_remote/Downloads/fw-script.sh
chmod 755 fw-script.sh
./fw-script.sh
```
Check the iptables rules again,
```bash
/sbin/iptables -n -L
```
You should see the new active rules.

Try pinging your desktop private virtual IP address from `cryptvm`:
```bash
ping 192.168.122.1
```
Try pinging `cryptvm` VM from the desktop:
```bash
ping cryptvm
```

To enable ping, you need to add the following rules to your `fw-script.sh` (you can include them somwhere after the default policy)

```{admonition} fw-script.sh:
    # Echo - uncomment to allow your system to be pinged.
    $IPT -A INPUT -p icmp -s 192.168.122.0/24 --icmp-type 0 -j ACCEPT
    $IPT -A INPUT -p icmp -s 192.168.122.0/24 --icmp-type 8 -j ACCEPT
    $IPT -A INPUT -p icmp -s 192.168.122.0/24 --icmp-type 11 -j ACCEPT
    $IPT -A OUTPUT -p icmp -d 192.168.122.0/24 --icmp-type 0 -j ACCEPT
    $IPT -A OUTPUT -p icmp -d 192.168.122.0/24 --icmp-type 8 -j ACCEPT
    $IPT -A OUTPUT -p icmp -d 192.168.122.0/24 --icmp-type 11 -j ACCEPT
    After the script is modified, you need to run the script,
```
Run it:
```bash
./fw-script.sh
```

Try to ssh to some host located outside of the lab, for example,  engsoft.rutgers.edu.
Try running `apt update` command.
Both SSH and apt would hang up because the iptable rules don't allow initiating outbound TCP connections with remote hosts and their returm from outside of the local virtual private network, 192.168.122.0/24.

To enable return TCP-connections from the outside of the subnet, change "-s 192.168.122.0/24" and "-d 192.168.122.0/24" for "-s 0/0" and "-d 0/0" in the rules for "Accept local-network return traffic..." in the script.
The new rules should look as follows:
```{admonition}
    $IPT -A INPUT -m state -p tcp --dport 1024:65535 --state ESTABLISHED,RELATED -s 0/0 -j ACCEPT
    $IPT -A OUTPUT -m state -p tcp --sport 1024:65535 ! --state INVALID -d 0/0 -j ACCEPT
```
After the script is modified, you need to run the script,
```bash
./fw-script.sh
```
Try ssh to the host and apt command again. They should run fine.

<hr>

## fail2ban (Exercise)

Fail2ban is a software that scans log files for brute force login attempts in real-time and bans the attackers with  iptables. This program works in the background and continuously scans the log files for unusual login patterns and security breach attempts. 

`Fail2ban` is similar to DenyHosts, however unlike DenyHosts which focuses on SSH, fail2ban can be configured to monitor any service that writes login attempts to a log file, and instead of using `/etc/hosts.deny` only to block IP addresses/hosts, `fail2ban` can use `iptables`.

`Fail2ban` installation on Ubuntu VM,  `cryptvm`.

First, flush the active iptables rules:
```bash
iptables -P INPUT   ACCEPT
iptables -P OUTPUT  ACCEPT
iptables -P FORWARD ACCEPT
iptables -F
```

Install fail2ban package:
```bash
apt install fail2ban
```

Backup the default configuration file
```bash
cp /etc/fail2ban/jail.conf /etc/fail2ban/jail.local
```

Create a new configuration file, `/etc/fail2ban/jail.d/sshd.local`, with the following content:
```bash
[sshd] 
enabled = true 
port = 22 
filter = sshd 
logpath = /var/log/auth.log 
maxretry = 5 
bantime = 86400
```
Restart fail2ban:
```bash
systemctl restart fail2ban
```
Check the active fail2ban status:
```bash
fail2ban-client status
```
Tru ssh to cryptvm from the other VM and use incorrect password 5 times.
Check the iptables settings on cryptvm:
```bash
iptables -nL 
```
Remove the banned IP address from the iptables, for example:
```bash
fail2ban-client set sshd unbanip 192.168.122.79
```

<hr>

## Port scanning (Exercise)

After unnecessary ports are closed and firewall implemented, the system should be scanned from a remote host with NMAP. Run nmap on the desktop to scan the ports on cryptvm.

To scan the TCP ports, for example on 192.168.122.42:
```bash
nmap -sT -O  192.168.122.42
```

```{admonition} ouput:
    The output may look like the following:
    Starting nmap  ( http://www.insecure.org/nmap/ ) at 2021-04-05 20:56 EDT
    Interesting ports on node18.linux.class (192.168.122.42):
    (The 1653 ports scanned but not shown below are in state: closed)
    PORT      STATE SERVICE
    22/tcp    open  ssh
    111/tcp   open  rpcbind
    139/tcp   open  netbios-ssn
    445/tcp   open  microsoft-ds
    513/tcp   open  login
    514/tcp   open  shell
    919/tcp   open  unknown
    953/tcp   open  rndc
    2049/tcp  open  nfs
    32772/tcp open  sometimes-rpc7
    MAC Address: 00:10:5A:0A:B3:E8 (3com)
    Device type: general purpose
    Running: Linux 2.4.X|2.5.X|2.6.X
    OS details: Linux 2.4.18 - 2.6.7
    Uptime 8.143 days (since Mon Mar 28 16:30:58 2021)
```

To scan the UDP ports, for example on 192.168.122.42:
```bash
nmap -sU -v  192.168.122.42
```
Nessus is an extension of NMAP; it provides vulnerability details and security advises.

Exercise.

Scan the TCP ports on cryptvm from your desktop:
```bash
nmap -sT -O  cryptvm
```

Scan the UDP ports on cryptvm from your desktop:
```bash
nmap -sU -v  cryptvm
```
<hr>

## References


[Password hashing with MD5-crypt in relation to MD5](http://www.vidarholen.net/contents/blog/?p=32)
 
[Implementation of SHA512-crypt vs MD5-crypt](http://www.vidarholen.net/contents/blog/?p=33)
 
[How are passwords stored in Linux (Understanding hashing with shadow utils)](http://www.slashroot.in/how-are-passwords-stored-linux-understanding-hashing-shadow-utils)

[How To Force Users To Use Strong Passwords In Debian, Ubuntu ](https://www.ostechnix.com/force-users-use-strong-passwords-debian-ubuntu)
 
[Configure SSH to use two-factor authentication](https://ubuntu.com/tutorials/configure-ssh-2fa#2-installing-and-configuring-required-packages)
 
[How to install fail2ban on Ubuntu Server 18.04 ](https://www.techrepublic.com/article/how-to-install-fail2ban-on-ubuntu-server-18-04)


[How to install Fail2Ban on CentOS 7](https://www.howtoforge.com/tutorial/how-to-install-fail2ban-on-centos)